培养码代码的好习惯，设置日志，打印程序运行中的细节，以便调试代码。



In [1]:
import logging
import os
import tempfile
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
TEMP_FOLDER = tempfile.gettempdir()
print('文件夹"{}" 将被用来存储语料和临时性的字典'.format(TEMP_FOLDER))

文件夹"C:\Users\GAOWEN~1\AppData\Local\Temp" 将被用来存储语料和临时性的字典


In [9]:
import gc, functools,time
import pickle, re
import random
from typing import List
from pprint import pprint
import pandas as pd

In [13]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy.spatial import distance
sns.set(style="whitegrid")
import gensim
import jieba
from tqdm import tqdm
from gensim.models.ldamodel import LdaModel

C:\Users\gaowenxin95\AppData\Roaming\Python\Python37\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [10]:
from gensim import corpora
import jieba

In [11]:
stopwords = open('../data/cn_stopwords.txt',encoding='utf-8').read().split()
stopwords = frozenset(stopwords)
print(len(stopwords))

746


In [12]:
dataset = pd.read_csv('../data/s1000.csv',encoding='utf-8')

In [14]:
from sklearn.model_selection import train_test_split

In [15]:
df=dataset['content']

In [16]:
df_train, df_test = train_test_split(df, test_size=0.3, random_state=45)

In [17]:
def seg_words(text):
    #去掉不在(所有中文、大小写字母、数字)中的非法字符
    regex = re.compile(r'[^\u4e00-\u9fa5]')
    text = regex.sub('', text) # 将非法字符用‘ ’替代
    text = text.strip() # 去掉前后的空格
    word_list = jieba.cut(text, cut_all= False)
    return word_list

In [18]:
train = df_train.apply(lambda x: " ".join(seg_words(str(x))))
test = df_test.apply(lambda x: " ".join(seg_words(str(x))))

Building prefix dict from the default dictionary ...
2020-07-11 20:21:56,229 : DEBUG : Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\GAOWEN~1\AppData\Local\Temp\jieba.cache
2020-07-11 20:21:56,231 : DEBUG : Loading model from cache C:\Users\GAOWEN~1\AppData\Local\Temp\jieba.cache
Loading model cost 0.670 seconds.
2020-07-11 20:21:56,901 : DEBUG : Loading model cost 0.670 seconds.
Prefix dict has been built succesfully.
2020-07-11 20:21:56,903 : DEBUG : Prefix dict has been built succesfully.


In [19]:
train.head(2)

640    是兆雄 在 日本 东京 的 三田 有 一幢 掩映 在 绿荫 之中 的 高层建筑 这 就是 新...
357    红旗 杂志 编辑部 人民日报 编辑部 世界 上 一切 革命斗争 都 是 为 着 夺取 政权 ...
Name: content, dtype: object

In [20]:
#将文档中可能存在的西文字符小写化，按空格进行拆分，且去停用词
train_texts = [[word for word in document.lower().split() if word not in stopwords]
         for document in train]

test_texts = [[word for word in document.lower().split() if word not in stopwords]
         for document in test]

In [21]:
train_texts[0:1]

[['是兆雄',
  '日本',
  '东京',
  '三田',
  '一幢',
  '掩映',
  '绿荫',
  '之中',
  '高层建筑',
  '新一代',
  '计算机',
  '技术开发',
  '研究所',
  '拥有',
  '渕',
  '一博',
  '所长',
  '为首',
  '四十余名',
  '专家',
  '研究',
  '人员',
  '承担',
  '研究',
  '领导',
  '研制',
  '第五代',
  '计算机',
  '艰巨',
  '任务',
  '早',
  '一九七九年',
  '日本',
  '通产省',
  '授意',
  '成立',
  '新一代',
  '计算机',
  '调查',
  '委员会',
  '一年',
  '考察',
  '研究',
  '提出',
  '新一代',
  '计算机',
  '概念',
  '一九八',
  '年',
  '东京',
  '召开',
  '新一代',
  '计算机',
  '国际',
  '讨论会',
  '一九八一年',
  '十月',
  '日本',
  '正式',
  '宣布',
  '研制',
  '第五代',
  '计算机',
  '一九八二年',
  '四月',
  '通产省',
  '召集',
  '全国',
  '从事',
  '电子计算机',
  '生产',
  '研究',
  '教学',
  '各大',
  '公司',
  '大学',
  '科研单位',
  '制定',
  '一项',
  '为期',
  '十年',
  '一九八',
  '二至',
  '一九九',
  '第五代',
  '计算机技术',
  '开发计划',
  '总',
  '投资',
  '一千',
  '亿日元',
  '第五代',
  '计算机技术',
  '开发计划',
  '主要',
  '内容',
  '包括',
  '开发',
  '解决问题',
  '推断',
  '知识',
  '基础',
  '管理',
  '智能',
  '接口',
  '计算机',
  '三大',
  '功能',
  '达到',
  '这一',
  '目标',
  '新一代',
  '计算机',
  '技术开发',
  '研究所',
  '决心',
  '解决',
  '基本'

In [25]:
dictionary = corpora.Dictionary(train_texts)
dictionary.save('../data/deerwester.dict')  # 保存字典，以备后续查找之用
print(dictionary)

2020-07-11 20:25:45,555 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2020-07-11 20:25:45,831 : INFO : built Dictionary(43475 unique tokens: ['一九七九年', '一九九', '一九八', '一九八一年', '一九八二年']...) from 700 documents (total 282306 corpus positions)
2020-07-11 20:25:45,833 : INFO : saving Dictionary object under ../data/deerwester.dict, separately None
2020-07-11 20:25:45,851 : INFO : saved ../data/deerwester.dict


Dictionary(43475 unique tokens: ['一九七九年', '一九九', '一九八', '一九八一年', '一九八二年']...)


In [23]:
print(dictionary.token2id)

{'一九七九年': 0, '一九九': 1, '一九八': 2, '一九八一年': 3, '一九八二年': 4, '一千': 5, '一博': 6, '一幢': 7, '一年': 8, '一项': 9, '三大': 10, '三田': 11, '专家': 12, '东京': 13, '为期': 14, '为首': 15, '主要': 16, '举行': 17, '之中': 18, '二十六': 19, '二至': 20, '人员': 21, '亿日元': 22, '仅为': 23, '今年': 24, '从事': 25, '以往': 26, '任务': 27, '体制': 28, '先后': 29, '全国': 30, '八位': 31, '公司': 32, '共同开发': 33, '共计': 34, '关键技术': 35, '内容': 36, '决心': 37, '制定': 38, '制成': 39, '功能': 40, '包括': 41, '十一月': 42, '十年': 43, '十月': 44, '协作': 45, '卫星': 46, '去年': 47, '参加': 48, '发回': 49, '取经': 50, '召开': 51, '召集': 52, '各国': 53, '各大': 54, '四分之一': 55, '四十余名': 56, '四所': 57, '四月': 58, '国外': 59, '国际': 60, '图像': 61, '图像处理': 62, '基本': 63, '基础': 64, '处理': 65, '外国': 66, '外国专家': 67, '大体': 68, '大型': 69, '大学': 70, '委员会': 71, '学习': 72, '学术交流': 73, '学者': 74, '完成': 75, '宗旨': 76, '宣布': 77, '尖端技术': 78, '工作': 79, '已有': 80, '已经': 81, '年': 82, '年底': 83, '广泛开展': 84, '应用': 85, '开发': 86, '开发计划': 87, '总': 88, '成立': 89, '所长': 90, '执行': 91, '承担': 92, '技术开发': 93, '投资': 94, '拥有': 95, '据统计': 96, '授意

In [28]:
corpus = [dictionary.doc2bow(text) for text in train_texts]
corpora.MmCorpus.serialize('../data/deerwester.mm', corpus)  #保存到本地，以作后用


2020-07-11 20:27:16,098 : INFO : storing corpus in Matrix Market format to ../data/deerwester.mm
2020-07-11 20:27:16,099 : INFO : saving sparse matrix to ../data/deerwester.mm
2020-07-11 20:27:16,100 : INFO : PROGRESS: saving document #0
2020-07-11 20:27:16,279 : INFO : saved 700x43475 matrix, density=0.547% (166340/30432500)
2020-07-11 20:27:16,280 : INFO : saving MmCorpus index to ../data/deerwester.mm.index


In [29]:
for c in corpus:
    print(c)

[(0, 1), (1, 1), (2, 4), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 2), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 2), (21, 2), (22, 1), (23, 1), (24, 2), (25, 1), (26, 1), (27, 2), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 1), (59, 1), (60, 3), (61, 1), (62, 1), (63, 2), (64, 2), (65, 1), (66, 1), (67, 1), (68, 1), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 2), (78, 1), (79, 1), (80, 1), (81, 2), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 3), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 3), (94, 1), (95, 1), (96, 1), (97, 1), (98, 1), (99, 1), (100, 1), (101, 3), (102, 1), (103, 1), (104, 1), (105, 1), (106, 1), (107, 6), (108, 4), (109, 1), (110, 1),

dictionary.filter_tokens（或者dictionary.add_document）将调用dictionary.compactify()来删除词汇id序列中的间隙，
空置的占位符（""）将会被剔除

In [30]:
print(dictionary[0])
print(dictionary[1])
print(dictionary[2])

一九七九年
一九九
一九八


In [32]:

from gensim import corpora,similarities,models

TF-IDF模型用以评估一字词对于一个文件集或一个语料库中的其中一份文件的重要程度，
它是一个标准的Python对象，可通过对语料库训练进行初始化。

In [33]:
tfidf = models.TfidfModel(corpus)   

2020-07-11 20:33:00,959 : INFO : collecting document frequencies
2020-07-11 20:33:00,960 : INFO : PROGRESS: processing document #0
2020-07-11 20:33:00,993 : INFO : calculating IDF weights for 700 documents and 43475 features (166340 matrix non-zeros)


In [43]:
corpus_tfidf = tfidf[corpus]

## 如何确定主题数

In [70]:

from gensim.models import CoherenceModel, LdaModel
import numpy
%matplotlib inline

In [71]:
numpy.random.seed(1) # 设置随即种子数，以便相同的设置能跑出相同的结果，可复现
goodLdaModel = LdaModel(corpus=corpus, id2word=dictionary,
     iterations=50, num_topics=2)
badLdaModel = LdaModel(corpus=corpus, id2word=dictionary, 
     iterations=50, num_topics=6)

2020-07-11 21:20:30,948 : INFO : using symmetric alpha at 0.5
2020-07-11 21:20:30,949 : INFO : using symmetric eta at 0.5
2020-07-11 21:20:30,958 : INFO : using serial LDA version on this node
2020-07-11 21:20:30,970 : INFO : running online (single-pass) LDA training, 2 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 21:20:30,971 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 21:20:31,984 : INFO : -11.142 per-word bound, 2259.8 perplexity estimate based on a held-out corpus of 700 documents with 282306 words
2020-07-11 21:20:31,985 : INFO : PROGRESS: pass 0, at document #700/700
2020-07-11 21:20:32,496 : INFO : topic #0 (0.500): 0.010*"日本" + 0.008*"人民" + 0.007*"中国" + 0.006*"中" + 0.004*"说" + 0.004*"发展" + 0.004*"美国" + 0.004*"年" + 0.0

### 使用U_Mass Coherence

In [72]:
goodcm = CoherenceModel(model=goodLdaModel, corpus=corpus, 
       dictionary=dictionary, coherence='u_mass')
badcm = CoherenceModel(model=badLdaModel, corpus=corpus,
       dictionary=dictionary, coherence='u_mass')

print(goodcm.get_coherence())
print(badcm.get_coherence())

-0.8964504065429089
-0.9122304546554426


虽然数值差异不大，但仍能看出“好”的主题模型的U_Mass Coherence要大于坏的模型的数值。

### 使用 C_V coherence

In [74]:
goodcm = CoherenceModel(model=goodLdaModel, texts=train_texts, 
    dictionary=dictionary,  coherence='c_v')
badcm = CoherenceModel(model=badLdaModel, texts=train_texts,
    dictionary=dictionary,  coherence='c_v')

print(goodcm.get_coherence())
print(badcm.get_coherence())

2020-07-11 21:23:37,038 : INFO : using ParallelWordOccurrenceAccumulator(processes=7, batch_size=64) to estimate probabilities from sliding windows
2020-07-11 21:23:42,183 : INFO : 1 batches submitted to accumulate stats from 64 documents (13308 virtual)
2020-07-11 21:23:42,188 : INFO : 2 batches submitted to accumulate stats from 128 documents (31446 virtual)
2020-07-11 21:23:42,194 : INFO : 3 batches submitted to accumulate stats from 192 documents (55806 virtual)
2020-07-11 21:23:42,201 : INFO : 4 batches submitted to accumulate stats from 256 documents (67180 virtual)
2020-07-11 21:23:42,210 : INFO : 5 batches submitted to accumulate stats from 320 documents (87615 virtual)
2020-07-11 21:23:42,217 : INFO : 6 batches submitted to accumulate stats from 384 documents (103943 virtual)
2020-07-11 21:23:42,235 : INFO : 7 batches submitted to accumulate stats from 448 documents (123861 virtual)
2020-07-11 21:23:42,275 : INFO : 8 batches submitted to accumulate stats from 512 documents (14

0.29797320099042957


2020-07-11 21:23:48,405 : INFO : 1 batches submitted to accumulate stats from 64 documents (13308 virtual)
2020-07-11 21:23:48,410 : INFO : 2 batches submitted to accumulate stats from 128 documents (31446 virtual)
2020-07-11 21:23:48,419 : INFO : 3 batches submitted to accumulate stats from 192 documents (55806 virtual)
2020-07-11 21:23:48,424 : INFO : 4 batches submitted to accumulate stats from 256 documents (67180 virtual)
2020-07-11 21:23:48,431 : INFO : 5 batches submitted to accumulate stats from 320 documents (87615 virtual)
2020-07-11 21:23:48,439 : INFO : 6 batches submitted to accumulate stats from 384 documents (103943 virtual)
2020-07-11 21:23:48,456 : INFO : 7 batches submitted to accumulate stats from 448 documents (123861 virtual)
2020-07-11 21:23:48,471 : INFO : 8 batches submitted to accumulate stats from 512 documents (140738 virtual)
2020-07-11 21:23:48,492 : INFO : 9 batches submitted to accumulate stats from 576 documents (161674 virtual)
2020-07-11 21:23:48,511 :

0.297758941138142


虽然数值差异不大，但“好”的主题模型的C_V coherence值仍要大于“坏”的主题模型的C_V coherence值。

### 利用复杂度prerplexity确定主题数

In [46]:
per_list=[]
ind=[]
def perlexity():
    for topicn in range(2,20):
        lda = models.LdaModel(corpus_tfidf, id2word = dictionary, num_topics = topicn)
        Perplexity=lda.log_perplexity(corpus)
        per_list.append(Perplexity)
        ind.append(topicn)
    return ind,per_list

In [47]:
ind,p=perlexity()

2020-07-11 20:52:10,567 : INFO : using symmetric alpha at 0.5
2020-07-11 20:52:10,569 : INFO : using symmetric eta at 0.5
2020-07-11 20:52:10,578 : INFO : using serial LDA version on this node
2020-07-11 20:52:10,589 : INFO : running online (single-pass) LDA training, 2 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 20:52:10,590 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 20:52:12,229 : INFO : -14.740 per-word bound, 27371.5 perplexity estimate based on a held-out corpus of 700 documents with 6843 words
2020-07-11 20:52:12,231 : INFO : PROGRESS: pass 0, at document #700/700
2020-07-11 20:52:12,731 : INFO : topic #0 (0.500): 0.000*"中国" + 0.000*"人民" + 0.000*"朝鲜" + 0.000*"美国" + 0.000*"亚洲" + 0.000*"发展" + 0.000*"美帝国主义" + 0.000*"说" +

2020-07-11 20:52:25,507 : INFO : topic #0 (0.167): 0.000*"中国" + 0.000*"人民" + 0.000*"代表团" + 0.000*"美国" + 0.000*"东盟" + 0.000*"北京" + 0.000*"发展" + 0.000*"中日" + 0.000*"关系" + 0.000*"日"
2020-07-11 20:52:25,509 : INFO : topic #5 (0.167): 0.000*"比赛" + 0.000*"中国" + 0.000*"世博会" + 0.000*"人民" + 0.000*"运动员" + 0.000*"日" + 0.000*"毛主席" + 0.000*"中日" + 0.000*"上海" + 0.000*"说"
2020-07-11 20:52:25,510 : INFO : topic diff=3.674217, rho=1.000000
2020-07-11 20:52:26,422 : INFO : -11.966 per-word bound, 4000.7 perplexity estimate based on a held-out corpus of 700 documents with 282306 words
2020-07-11 20:52:26,425 : INFO : using symmetric alpha at 0.14285714285714285
2020-07-11 20:52:26,426 : INFO : using symmetric eta at 0.14285714285714285
2020-07-11 20:52:26,433 : INFO : using serial LDA version on this node
2020-07-11 20:52:26,466 : INFO : running online (single-pass) LDA training, 7 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity ev

2020-07-11 20:52:38,063 : INFO : topic diff=6.987527, rho=1.000000
2020-07-11 20:52:39,122 : INFO : -13.094 per-word bound, 8745.0 perplexity estimate based on a held-out corpus of 700 documents with 282306 words
2020-07-11 20:52:39,124 : INFO : using symmetric alpha at 0.09090909090909091
2020-07-11 20:52:39,125 : INFO : using symmetric eta at 0.09090909090909091
2020-07-11 20:52:39,130 : INFO : using serial LDA version on this node
2020-07-11 20:52:39,180 : INFO : running online (single-pass) LDA training, 11 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 20:52:39,181 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 20:52:40,847 : INFO : -94.465 per-word bound, 27334544673680528185025888256.0 perplexity estimate based on a held-ou

2020-07-11 20:52:52,361 : INFO : -14.033 per-word bound, 16764.5 perplexity estimate based on a held-out corpus of 700 documents with 282306 words
2020-07-11 20:52:52,363 : INFO : using symmetric alpha at 0.06666666666666667
2020-07-11 20:52:52,364 : INFO : using symmetric eta at 0.06666666666666667
2020-07-11 20:52:52,369 : INFO : using serial LDA version on this node
2020-07-11 20:52:52,433 : INFO : running online (single-pass) LDA training, 15 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 20:52:52,434 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 20:52:54,161 : INFO : -146.825 per-word bound, 158029571097244964159247784454322284587384832.0 perplexity estimate based on a held-out corpus of 700 documents with 6843 words
2020-07

2020-07-11 20:53:06,628 : INFO : using symmetric alpha at 0.05263157894736842
2020-07-11 20:53:06,629 : INFO : using symmetric eta at 0.05263157894736842
2020-07-11 20:53:06,637 : INFO : using serial LDA version on this node
2020-07-11 20:53:06,718 : INFO : running online (single-pass) LDA training, 19 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 20:53:06,719 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 20:53:08,424 : INFO : -205.550 per-word bound, 75265333734153610514751302786164409993855525718831591061454848.0 perplexity estimate based on a held-out corpus of 700 documents with 6843 words
2020-07-11 20:53:08,425 : INFO : PROGRESS: pass 0, at document #700/700
2020-07-11 20:53:09,056 : INFO : topic #0 (0.053): 0.000*"世博会" + 

In [48]:
for (x,y) in zip(ind,p):
    print(x,y)

2 -10.714459750247492
3 -11.010150248077583
4 -11.309914415250145
5 -11.617391741633535
6 -11.966052164352204
7 -12.217162871504266
8 -12.530418268027663
9 -12.815931865000142
10 -13.094237621551029
11 -13.312708954269729
12 -13.534552403188709
13 -13.790094784943676
14 -14.033120825921458
15 -14.240975639349868
16 -14.383836414556065
17 -14.616622484960262
18 -14.776541689183137
19 -14.953212704196622


## 使用词袋模型表示向量并进行转化

In [35]:
corpus_tfidf = tfidf[corpus]
for doc in corpus_tfidf:
    print(doc)

[(0, 0.062282335131281105), (1, 0.06965196941293822), (2, 0.2318855017299304), (3, 0.0579713754324826), (4, 0.06965196941293822), (5, 0.04629078145202697), (6, 0.06965196941293822), (7, 0.06965196941293822), (8, 0.024181878607055615), (9, 0.026853887493592302), (10, 0.04238108200892003), (11, 0.062282335131281105), (12, 0.026853887493592302), (13, 0.033041869475181646), (14, 0.04238108200892003), (15, 0.033850426131607304), (16, 0.01569203711702792), (17, 0.013753569742539882), (18, 0.03247662958072459), (19, 0.04896279033856366), (20, 0.12456467026256221), (21, 0.05021399059813495), (22, 0.041593156056906534), (23, 0.062282335131281105), (24, 0.03233535034429771), (25, 0.03280379800465263), (26, 0.04085961454485788), (27, 0.04836375721411123), (28, 0.03586247258751124), (29, 0.024947110559350946), (30, 0.01562579307200596), (31, 0.06965196941293822), (32, 0.024181878607055615), (33, 0.06965196941293822), (34, 0.04896279033856366), (35, 0.0579713754324826), (36, 0.02526932112129532), (

[(47, 0.020348631872536917), (108, 0.00113010371726738), (134, 0.032763545475554004), (156, 0.007282596253834022), (221, 0.019726110668390837), (226, 0.03378584863929415), (231, 0.02274208406143289), (241, 0.02617381270784775), (265, 0.02076523044112502), (273, 0.022489694421667154), (379, 0.02439551424070269), (579, 0.019096639743726856), (690, 0.03926499737626688), (726, 0.04174391666907867), (739, 0.031536372636159965), (783, 0.09339947788809795), (793, 0.014687166030159711), (931, 0.04735074745700422), (1036, 0.024101631068377868), (1083, 0.03437318580805933), (1161, 0.029677848927477248), (1205, 0.03730302188249611), (1306, 0.030971712540000973), (1459, 0.029677848927477248), (1501, 0.025999401307455768), (1558, 0.01666688950059577), (1691, 0.020246962250751423), (1705, 0.044004124103613436), (1938, 0.0675716972785883), (1999, 0.05104878396375432), (2012, 0.02274208406143289), (2095, 0.07274269852152034), (2164, 0.02353697097221888), (2269, 0.05496242157755888), (2454, 0.028306699

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



可以看到，每个转换后的语句中，单个词汇的表示由整数型数值的词汇计数转变成了浮点型的词汇权重。该权重表示字词对于该语句的重要性程度，数值越大，则重要性程度越高，反之越小，对于其原理，可以进行如此直觉性的理解：
字词的重要性随着它在文件中出现的次数成正比增加，但同时会随着它在语料库中出现的频率成反比下降。

## LSI/LSA

详细推导原理见：https://www.cnblogs.com/pinard/p/6805861.html

In [36]:
LSI = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=3) # 初始化 LSI 转换
corpus_lsi = LSI[corpus_tfidf]  
#在原始语料词袋表示的基础上创建一个双包装器（Double Wrapper）：bow-> tfidf-> lsi    

2020-07-11 20:39:58,971 : INFO : using serial LSI version on this node
2020-07-11 20:39:58,973 : INFO : updating model with new documents
2020-07-11 20:39:59,616 : INFO : preparing a new chunk of documents
2020-07-11 20:39:59,651 : INFO : using 100 extra samples and 2 power iterations
2020-07-11 20:39:59,652 : INFO : 1st phase: constructing (43475, 103) action matrix
2020-07-11 20:39:59,702 : INFO : orthonormalizing (43475, 103) action matrix
2020-07-11 20:40:01,699 : INFO : 2nd phase: running dense svd on (103, 700) matrix
2020-07-11 20:40:01,765 : INFO : computing the final decomposition
2020-07-11 20:40:01,767 : INFO : keeping 3 factors (discarding 86.363% of energy spectrum)
2020-07-11 20:40:01,777 : INFO : processed documents up to #700
2020-07-11 20:40:01,783 : INFO : topic #0(3.565): 0.240*"人民" + 0.142*"朝鲜" + 0.141*"斗争" + 0.138*"美帝国主义" + 0.133*"中国" + 0.119*"反对" + 0.116*"和平" + 0.111*"美国" + 0.095*"发展" + 0.092*"经济"
2020-07-11 20:40:01,785 : INFO : topic #1(2.407): -0.268*"人民" + -0.

In [37]:
LSI.show_topics()

[(0,
  '0.240*"人民" + 0.142*"朝鲜" + 0.141*"斗争" + 0.138*"美帝国主义" + 0.133*"中国" + 0.119*"反对" + 0.116*"和平" + 0.111*"美国" + 0.095*"发展" + 0.092*"经济"'),
 (1,
  '-0.268*"人民" + -0.231*"美帝国主义" + -0.197*"朝鲜" + -0.186*"斗争" + 0.149*"经济" + -0.135*"反对" + 0.125*"中日" + 0.118*"发展" + 0.104*"中国" + -0.103*"侵略"'),
 (2,
  '-0.217*"代表团" + -0.171*"会见" + -0.168*"友好" + -0.157*"中日" + -0.123*"访问" + -0.116*"团长" + -0.110*"协会" + 0.108*"革命" + -0.104*"日中" + -0.102*"北京"')]

由于LSI、LDA等主题模型在本质上属于软聚类（Soft Clustering），也就是说，每个主题上的概率就是文章对于这个主题的隶属度，
同一个文档可能夹杂着多个主题，只是对应的各个主题的概率不同罢了。

In [39]:
LSI.save('../data/model.lsi')

2020-07-11 20:42:40,456 : INFO : saving Projection object under ../data/model.lsi.projection, separately None
2020-07-11 20:42:40,469 : INFO : saved ../data/model.lsi.projection
2020-07-11 20:42:40,470 : INFO : saving LsiModel object under ../data/model.lsi, separately None
2020-07-11 20:42:40,470 : INFO : not storing attribute projection
2020-07-11 20:42:40,471 : INFO : not storing attribute dispatcher
2020-07-11 20:42:40,496 : INFO : saved ../data/model.lsi


### 增量学习方法

- model.add_documents(another_tfidf_corpus)  
现在LSI模型已经在tfidf_corpus + 另一个tfidf_corpus上进行训练了
- lsi_vec = model[tfidf_vec]              
 将一个新文档转换到LSI空间，但不影响模型
- model.add_documents(more_documents)     
 tfidf_corpus + another_tfidf_corpus + 更多的文档 lsi_vec = model[tfidf_vec]

## Random Projections

RP算法旨在减少向量空间的维度。 这是一种非常有效的（对内存和CPU友好）方法，
通过加入一点随机性来近似表示文档之间的TF-IDF距离。
比较推荐的目标维度最好是几百/几千，具体数值取决于语料库的大小。

In [40]:
RPmodel = models.RpModel(corpus_tfidf, num_topics=3)

2020-07-11 20:47:48,691 : INFO : no word id mapping provided; initializing from corpus, assuming identity
2020-07-11 20:47:49,326 : INFO : constructing (3, 43475) random matrix


In [41]:
RPmodel.num_topics #主题数有多少？

3

In [42]:
RPmodel.num_terms  #主题模型中参与训练的词汇数有多少？

43475

## LDA

In [49]:
LDAmodel = models.LdaModel(corpus, id2word=dictionary, num_topics=20)

2020-07-11 20:55:30,601 : INFO : using symmetric alpha at 0.05
2020-07-11 20:55:30,602 : INFO : using symmetric eta at 0.05
2020-07-11 20:55:30,611 : INFO : using serial LDA version on this node
2020-07-11 20:55:30,699 : INFO : running online (single-pass) LDA training, 20 topics, 1 passes over the supplied corpus of 700 documents, updating model once every 700 documents, evaluating perplexity every 700 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-11 20:55:30,701 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2020-07-11 20:55:32,098 : INFO : -16.391 per-word bound, 85912.2 perplexity estimate based on a held-out corpus of 700 documents with 282306 words
2020-07-11 20:55:32,100 : INFO : PROGRESS: pass 0, at document #700/700
2020-07-11 20:55:33,048 : INFO : topic #13 (0.050): 0.010*"人民" + 0.007*"中国" + 0.006*"发展" + 0.005*"中" + 0.005*"国家" + 0.004*"日本" + 0.004*"说" + 0.003*"经济"

In [50]:
LDAmodel.show_topics()

[(11,
  '0.011*"人民" + 0.007*"中国" + 0.007*"中" + 0.005*"日本" + 0.005*"说" + 0.005*"发展" + 0.004*"国家" + 0.004*"进行" + 0.003*"资产阶级" + 0.003*"反对"'),
 (1,
  '0.009*"日本" + 0.005*"年" + 0.004*"月" + 0.004*"问题" + 0.004*"人民" + 0.004*"一个" + 0.003*"中" + 0.003*"美国" + 0.003*"中国" + 0.003*"说"'),
 (8,
  '0.005*"中" + 0.004*"人民" + 0.004*"日本" + 0.004*"年" + 0.003*"我国" + 0.003*"中国" + 0.003*"国家" + 0.003*"世界" + 0.003*"问题" + 0.003*"新"'),
 (12,
  '0.008*"中国" + 0.005*"人民" + 0.005*"发展" + 0.005*"日本" + 0.004*"年" + 0.004*"说" + 0.004*"中" + 0.004*"青年" + 0.004*"美国" + 0.003*"国家"'),
 (16,
  '0.008*"日本" + 0.005*"中国" + 0.004*"人民" + 0.004*"中" + 0.003*"说" + 0.003*"一个" + 0.003*"进行" + 0.003*"国家" + 0.002*"月" + 0.002*"新"'),
 (7,
  '0.014*"中国" + 0.007*"日本" + 0.005*"发展" + 0.004*"中" + 0.004*"说" + 0.004*"人民" + 0.004*"进行" + 0.004*"经济" + 0.003*"国家" + 0.003*"国际"'),
 (19,
  '0.018*"日本" + 0.011*"人民" + 0.010*"中国" + 0.006*"中" + 0.005*"说" + 0.004*"一个" + 0.004*"年" + 0.004*"进行" + 0.004*"美国" + 0.004*"发展"'),
 (6,
  '0.007*"中国" + 0.005*"人民" + 0.005*"中

## 层次狄利克雷过程（Hierarchical Dirichlet Process, HDP）

HDP是一种非参数贝叶斯方法（跟其他的主题模型不同，它不需要事先确定主题的数量），
它对于想偷懒的同学来说，简直是福音！以下是它的接口调用方法：

In [51]:
HDPmodel = models.HdpModel(corpus, id2word=dictionary)

2020-07-11 20:57:54,066 : INFO : (0, '0.016*人民 + 0.008*中国 + 0.007*中 + 0.006*日本 + 0.005*斗争 + 0.005*社会主义 + 0.004*革命 + 0.004*美国 + 0.004*进行 + 0.004*说')
2020-07-11 20:57:54,099 : INFO : (1, '0.010*日本 + 0.009*人民 + 0.007*中国 + 0.005*说 + 0.005*国家 + 0.004*中 + 0.004*和平 + 0.004*美国 + 0.003*问题 + 0.003*斗争')
2020-07-11 20:57:54,135 : INFO : (2, '0.006*中国 + 0.005*日本 + 0.004*年 + 0.004*中 + 0.003*国家 + 0.003*发展 + 0.003*世界 + 0.003*美国 + 0.003*问题 + 0.003*一个')
2020-07-11 20:57:54,169 : INFO : (3, '0.009*发展 + 0.006*经济 + 0.005*日本 + 0.005*中国 + 0.004*年 + 0.003*企业 + 0.003*说 + 0.003*国际 + 0.003*问题 + 0.003*创新')
2020-07-11 20:57:54,203 : INFO : (4, '0.007*中国 + 0.005*日本 + 0.004*中 + 0.004*说 + 0.003*人民 + 0.003*月 + 0.003*亚洲 + 0.002*进行 + 0.002*年 + 0.002*美国')
2020-07-11 20:57:54,235 : INFO : (5, '0.005*发展 + 0.004*工作 + 0.004*生产 + 0.004*年 + 0.004*农业 + 0.004*我国 + 0.003*说 + 0.003*中 + 0.003*问题 + 0.003*一个')
2020-07-11 20:57:54,268 : INFO : (6, '0.004*年 + 0.004*说 + 0.004*一个 + 0.003*联欢节 + 0.003*中国 + 0.003*青年 + 0.003*参加 + 0.003*同志 + 

In [54]:
HDPmodel.get_topics 

<bound method HdpModel.get_topics of <gensim.models.hdpmodel.HdpModel object at 0x000001E3A0D7C518>>

In [55]:
HDPmodel.show_topics

<bound method HdpModel.show_topics of <gensim.models.hdpmodel.HdpModel object at 0x000001E3A0D7C518>>

## 检索相似语句

In [57]:
#将查询语料库转换到LSI向量空间并对其中的每个文档/语句建立索引
index = similarities.MatrixSimilarity(LDAmodel[corpus])  
#将查询语料库转换到LSI向量空间并对其中的每个文档/语句建立索引
#index = similarities.Similarity(output_prefix='Similarity',corpus=lsi[corpus],num_features=500)  

2020-07-11 21:02:42,932 : WARNING : scanning corpus to determine the number of features (consider setting `num_features` explicitly)
2020-07-11 21:02:43,613 : INFO : creating matrix with 700 documents and 20 features


In [69]:
# 产生BOW向量
vec = dictionary.doc2bow(test)
test_vec = LDAmodel[vec]
# 计算相似度
sim = index.get_similarities(test_vec)
related_doc_indices = sim.argsort()[:-10:-1]
print(related_doc_indices)

[648 144 343 316   4 171 434 391 529]


## 可视化

In [ ]:
import warnings
try:
    import pyLDAvis.gensim
    CAN_VISUALIZE = True
    pyLDAvis.enable_notebook()
    from IPython.display import display
except ImportError:
    ValueError("SKIP: please install pyLDAvis")
    CAN_VISUALIZE = False
warnings.filterwarnings('ignore')  # 忽视所有的提示
%matplotlib inline

prepared = pyLDAvis.gensim.prepare(LDAmodel, corpus, dictionary)
pyLDAvis.show(prepared,open_browser=True)
 


Note: if you're in the IPython notebook, pyLDAvis.show() is not the best command
      to use. Consider using pyLDAvis.display(), or pyLDAvis.enable_notebook().
      See more information at http://pyLDAvis.github.io/quickstart.html .

You must interrupt the kernel to end this command

Serving to http://127.0.0.1:8889/    [Ctrl-C to exit]


127.0.0.1 - - [11/Jul/2020 21:30:39] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [11/Jul/2020 21:30:39] "GET /LDAvis.css HTTP/1.1" 200 -
127.0.0.1 - - [11/Jul/2020 21:30:39] "GET /d3.js HTTP/1.1" 200 -
127.0.0.1 - - [11/Jul/2020 21:30:39] "GET /LDAvis.js HTTP/1.1" 200 -
127.0.0.1 - - [11/Jul/2020 21:30:39] code 404, message Not Found
127.0.0.1 - - [11/Jul/2020 21:30:39] "GET /favicon.ico HTTP/1.1" 404 -
